# Internal testing clean room sample

This notebook demonstrates how to create and run a clean room using a single Snowflake account, rather than using separate accounts for the provider and consumer.

Internal testing clean rooms are useful for developers who don't have easy access to two Snowflake accounts, or for running quick tests where you don't want to open separate code windows for the provider and consumer.

Internal testing clean rooms support most, but not all clean room features, and cannot be shared with other consumers later. [Learn more about internal testing clean rooms](https://docs.snowflake.com/user-guide/cleanrooms/developer-introduction#label-dcr-self-share-for-developers).

## Requirements

You must have a Snowflake account with the clean rooms environment installed to run this example, and you must be able to use the SAMOOHA_APP_ROLE role.

## More information

- Read the [getting started guide](https://docs.snowflake.com/en/user-guide/cleanrooms/getting-started) for a high level overview of all the steps here.
- Read the [API tutorial](https://docs.snowflake.com/user-guide/cleanrooms/tutorials/cleanroom-api-tutorial-basic), which gives more information about the steps shown here, with code snippets.

## Set up your environment

You need to use a warehouse with clean room access, and use the samooha_app_role role. Clean rooms installs the app_wh warehouse, which has clean rooms API privileges.

In [ ]:
USE WAREHOUSE app_wh;
USE ROLE samooha_app_role;

# Provider

You will start off acting as the provider to create, configure, share, and deploy the clean room.

## Create the clean room

You start by acting as the provider, and creating a clean room:

In [ ]:
SET cleanroom_name = (SELECT current_user || ' internal testing clean room');
SET account_locator = (select current_account());
SET account_identifier = (select current_organization_name() || '.' || current_account_name());
CALL samooha_by_snowflake_local_db.provider.cleanroom_init($cleanroom_name, 'INTERNAL');

When the previous code completes, you can see the new clean room in your account as a provider, along with any other clean rooms that were created in your account.

In [ ]:
CALL samooha_by_snowflake_local_db.provider.view_cleanrooms();

## Link in data

Now you will *link* (import) data into the clean room. This workbook uses sample data installed with the clean room account. This data is already [registered](https://docs.snowflake.com/user-guide/cleanrooms/register-data), so you don't need to register it before you link it.

In [ ]:
CALL samooha_by_snowflake_local_db.provider.link_datasets($cleanroom_name, ['SAMOOHA_SAMPLE_DATABASE.DEMO.CUSTOMERS']);

## Set provider join policies

Next you will set a join policy on your linked data. A clean room join policy specifies which columns can be joined on by consumer queries. The code below lets the consumer join on the `HASHED_EMAIL` and `HASHED_PHONE` columns from your data. Join columns can't be projected, only joined on.

In [ ]:
CALL samooha_by_snowflake_local_db.provider.set_join_policy(
  $cleanroom_name,
  ['SAMOOHA_SAMPLE_DATABASE.DEMO.CUSTOMERS:HASHED_EMAIL',
   'SAMOOHA_SAMPLE_DATABASE.DEMO.CUSTOMERS:HASHED_PHONE']);

View the join policy that you just created:

In [ ]:
CALL samooha_by_snowflake_local_db.provider.view_join_policy($cleanroom_name);

## Install a template

You will install a template into the clean room. A template is a JinjaSQL template that evaluates to a SQL query at run time, depending on values submitted by the consumer.

By default, consumers can run any template that you install. You will install a test template named "prod_overlap_analysis" that comes with the clean room environment. This template shows the overlap between a provider and consumer table by a specified column, and provides aggregated data for the specified column.

In [ ]:
SET template_name = 'prod_overlap_analysis';
CALL samooha_by_snowflake_local_db.provider.add_templates(
  $cleanroom_name,
  [$template_name]);

View the code of the template that you just installed:

In [ ]:
CALL samooha_by_snowflake_local_db.provider.view_template_definition(
  $cleanroom_name,
  $template_name);

## Set provider column policies

You now set column policies, which specify which columns of your data the consumer can project. Column policies specify column-template pairs; meaning that a column policy specifies which columns can be projected in which templates. If a consumer tries to project a provider column in a template that isn't permitted by the provider's column policies, the analysis will fail.

The following code specifies four columns that can be projected when using the "prod_overlap_analysis" template.

In [ ]:
CALL samooha_by_snowflake_local_db.provider.set_column_policy(
  $cleanroom_name, 
  [
    $template_name || ':SAMOOHA_SAMPLE_DATABASE.DEMO.CUSTOMERS:STATUS',
    $template_name || ':SAMOOHA_SAMPLE_DATABASE.DEMO.CUSTOMERS:AGE_BAND',
    $template_name || ':SAMOOHA_SAMPLE_DATABASE.DEMO.CUSTOMERS:DAYS_ACTIVE',
    $template_name || ':SAMOOHA_SAMPLE_DATABASE.DEMO.CUSTOMERS:REGION_CODE']);


View the policy that you just created:

In [ ]:
CALL samooha_by_snowflake_local_db.provider.view_column_policy($cleanroom_name);

## Share with consumers

Next, you will specify which consumers can access this clean room when it is published. Consumers are referenced by a combination of account locator and data sharing account ID. You will add your own account in this case, making this an internal testing clean room. Internal testing clean rooms must be within the same organization, and you can never share it with another account.

In [ ]:
CALL samooha_by_snowflake_local_db.provider.add_consumers(
  $cleanroom_name,
  $account_locator,
  $account_identifier);

## Set the default release directive

This specifies the patch version of the application served by the user. Since we not added code to the clean room, it starts at the first patch number, which is V1.0.0.

In [ ]:
CALL samooha_by_snowflake_local_db.provider.set_default_release_directive(
  $cleanroom_name,
  'V1_0',
  '0');

## Publish the clean room

When this procedure returns, it can be installed and used by all consumer with which it was shared. This procedure can take a minute or two to run.

In [ ]:
CALL samooha_By_snowflake_local_db.provider.create_or_update_cleanroom_listing($cleanroom_name);

Take a look at what you just created.

In [ ]:
-- Describe the clean room
CALL samooha_by_snowflake_local_db.provider.describe_cleanroom($cleanroom_name);

# Consumer

Now put on your consumer hat, and get ready to install and run the clean room.

## Install the clean room

A consumer must install the clean room to run it. Clean rooms are implemented as native apps, with a provider and a consumer side, so a consumer must install a clean room to use it, even in an internal testing implementation.

Installing a clean room takes a minute or two.

In [ ]:
CALL samooha_by_snowflake_local_db.consumer.install_cleanroom(
  $cleanroom_name,
  $account_locator);

## Link in your data

For simplicity, you will link in the same sample dataset that the provider linked, although the overlap will be 100%. 

In [ ]:
CALL samooha_by_snowflake_local_db.consumer.link_datasets(
  $cleanroom_name,
  ['SAMOOHA_SAMPLE_DATABASE.DEMO.CUSTOMERS']);

# See the provider's data and policies

You can look to see what data the provider linked in, as well as the provider's join and column policies. Note that these procedures all use the `consumer` namespace. This means you are calling these procedures from the perspective of a consumer, not a provider.

See what data the provider added to the clean room:

In [ ]:
CALL samooha_by_snowflake_local_db.consumer.view_provider_datasets(
  $cleanroom_name);

See what columns the provider lets you join on:

In [ ]:
CALL samooha_by_snowflake_local_db.consumer.view_provider_join_policy(
  $cleanroom_name);

See what columns the provider lets you project:

In [ ]:
CALL samooha_by_snowflake_local_db.consumer.view_provider_column_policy(
  $cleanroom_name);

See what templates the provider added to the clean room:

In [ ]:
CALL samooha_by_snowflake_local_db.consumer.view_added_templates(
  $cleanroom_name);

See what arguments you can pass to the template:

In [ ]:
CALL samooha_by_snowflake_local_db.consumer.get_arguments_from_template(
  $cleanroom_name,
  $template_name);

## Run an analysis

Finally, you're ready to run an analysis. Specify values for `dimensions`, `measure_column`, `measure_type`, and `where_clause`, as well as which provider table and which of your tables to use in the analysis.

Note that the column names are prefixed by `p` and `c`, which are table aliases for the provider and consumer tables, respectively. You need to do this because of the way the query is written.

In [ ]:
CALL samooha_by_snowflake_local_db.consumer.run_analysis(
  $cleanroom_name,
  'prod_overlap_analysis',
  ['SAMOOHA_SAMPLE_DATABASE.DEMO.CUSTOMERS'], -- Consumer tables.
  ['SAMOOHA_SAMPLE_DATABASE.DEMO.CUSTOMERS'], -- Provider tables.
  object_construct(                           -- Extra template-specific arguments here as name-value pairs.
    'dimensions', ['p.STATUS'],          -- GROUP BY columns to show in the results.
    'measure_column', ['p.HOUSEHOLD_SIZE'], -- Aggregation columns to show in the results.
    'measure_type', ['AVG'],             -- Aggregation functions to apply to measure_column columns.
    'where_clause', 'p.HASHED_EMAIL=c.HASHED_EMAIL'
  )
);


You can try the query using other columns.

# Clean up

When you're done, delete the clean room for both the provider and consumer. This is important not only to prevent clogging your clean room pool with abandoned clean rooms, but also because there is a limit to the number of clean rooms that an account can hold; if you leave a lot of unused clean rooms during development, you can hit that limit and will have lots of cleanup to do later.

In [ ]:
-- Delete the clean room from the consumer's account.
CALL samooha_by_snowflake_local_db.consumer.uninstall_cleanroom($cleanroom_name);

-- Delete the clean room from the provider's account.
CALL samooha_by_snowflake_local_db.provider.drop_cleanroom($cleanroom_name);

# Next steps

There's a lot more to learn about clean rooms. Here are some starting places where you can learn more about developing Snowflake Data Clean Rooms:

- [The getting started guide](https://docs.snowflake.com/user-guide/cleanrooms/getting-started), which provides a high-level overview and lots of useful links for more details.
- [The API tutorial](https://docs.snowflake.com/user-guide/cleanrooms/tutorials/cleanroom-api-tutorial-basic) for a walk through of creating a clean room, with some more details.
- [The developer introduction](https://docs.snowflake.com/user-guide/cleanrooms/developer-introduction) for more details on how to program using the clean rooms API.